In [45]:
!pip install geojson

In [ ]:
import matplotlib.pyplot as plt
import geopandas as gpd
import json
from shapely.geometry import shape, GeometryCollection
from geojson import dump
import os
from tqdm import tqdm
import pandas as pd

# https://stackoverflow.com/questions/56605238/how-to-use-tqdm-for-json-file-load-progress-bar
def hook(obj):
    value = obj.get("features")
    if not value:
        return obj
    pbar = tqdm(value)
    for _ in pbar:
        pbar.set_description(f"Loading")
    return obj


def simplify_geojson(path: str, tolerance: float):
    with open(path) as f:
        features = json.load(f, object_hook=hook)["features"]

    file_stats = os.stat(path)
    print(f'{path} Size in MegaBytes is {file_stats.st_size / (1024 * 1024)}')

    geom = GeometryCollection([shape(feature["geometry"]).buffer(0) for feature in features])
    polys = []
    pre = 0
    post = 0

    p = gpd.GeoSeries(geom)
    p.plot(figsize=(30, 10))
    plt.show()

    for p in geom.geoms:
        poly = p
        if poly.geom_type == 'Polygon':
            x = len(poly.exterior.coords)
        elif poly.geom_type == 'MultiPolygon':
            x = sum([len(poly_item.exterior.coords) for poly_item in poly.geoms])
        pre += x

        poly = poly.simplify(tolerance=tolerance)
        if poly.geom_type == 'Polygon':
            a = len(poly.exterior.coords)
        elif poly.geom_type == 'MultiPolygon':
            a = sum([len(poly_item.exterior.coords) for poly_item in poly.geoms])
        post += a

        polys.append(poly)

    print(f'Simplified {pre} polygons to {post}')
    p = gpd.GeoSeries(polys)
    p.plot(figsize=(30, 10))
    plt.show()

    new_filename = f'{path}_compressed_{tolerance}.geojson'
    with open(new_filename, 'w') as f:
        dump(GeometryCollection(polys), f)

    file_stats = os.stat(f'{path}_compressed_{tolerance}.geojson')
    print(f'{new_filename} Size in MegaBytes is {file_stats.st_size / (1024 * 1024)}')

simplify_geojson('data/geocells/admin_1.geojson', 2.5)
simplify_geojson('data/geocells/admin_2.geojson', 2.5)
simplify_geojson('data/geocells/countries.geojson', 2.5)


# Show geocells
# df = pd.read_csv(f"data/geocells/geocells_yfcc(1).csv", index_col=False)
# df['geometry'] = gpd.GeoSeries.from_wkt(df['geometry'])
# geom = GeometryCollection([shape(x).buffer(0) for x in df['geometry']])
# p = gpd.GeoSeries(geom)
# p.plot(figsize=(30, 10))
# plt.show()

Loading: 100%|██████████| 218/218 [00:00<00:00, 443.02it/s]


data/geocells/countries.geojson Size in MegaBytes is 382.61291885375977


Simplified 10075273 polygons to 23479


data/geocells/countries.geojson_compressed_2.5.geojson Size in MegaBytes is 0.9441022872924805
